<a href="https://colab.research.google.com/github/fahriyegrl/ISIC-2024_skin_cancer_detection/blob/main/ISIC_2024_skin_cancer_detection.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [2]:

import torchvision.transforms as transforms
from sklearn.preprocessing import StandardScaler
from torch.utils.data import Dataset
import pandas as pd
import h5py


train_metadata = pd.read_csv('https://media.githubusercontent.com/media/fahriyegrl/ISIC-2024_skin_cancer_detection/master/train-metadata.csv')
test_metadata = pd.read_csv('https://raw.githubusercontent.com/fahriyegrl/ISIC-2024_skin_cancer_detection/main/test-metadata.csv')

train_metadata.head(), test_metadata.head()


<ipython-input-2-c3f34127e8fd>:8: DtypeWarning: Columns (51,52) have mixed types. Specify dtype option on import or set low_memory=False.
  train_metadata = pd.read_csv('https://media.githubusercontent.com/media/fahriyegrl/ISIC-2024_skin_cancer_detection/master/train-metadata.csv')


(        isic_id  target  patient_id  age_approx   sex anatom_site_general  \
 0  ISIC_0015670       0  IP_1235828        60.0  male     lower extremity   
 1  ISIC_0015845       0  IP_8170065        60.0  male           head/neck   
 2  ISIC_0015864       0  IP_6724798        60.0  male     posterior torso   
 3  ISIC_0015902       0  IP_4111386        65.0  male      anterior torso   
 4  ISIC_0024200       0  IP_8313778        55.0  male      anterior torso   
 
    clin_size_long_diam_mm          image_type tbp_tile_type   tbp_lv_A  ...  \
 0                    3.04  TBP tile: close-up     3D: white  20.244422  ...   
 1                    1.10  TBP tile: close-up     3D: white  31.712570  ...   
 2                    3.40  TBP tile: close-up        3D: XP  22.575830  ...   
 3                    3.22  TBP tile: close-up        3D: XP  14.242329  ...   
 4                    2.73  TBP tile: close-up     3D: white  24.725520  ...   
 
     lesion_id  iddx_full  iddx_1  iddx_2  iddx_

In [3]:
#Data transformation

skin_transform =  transforms.Compose([
    transforms.Resize((224,224)),
    transforms.ToTensor(),
    transforms.Normalize(mean=[0.5, 0.5, 0.5], std=[0.5, 0.5, 0.5])
])


In [4]:
!wget https://media.githubusercontent.com/media/fahriyegrl/ISIC-2024_skin_cancer_detection/master/train-metadata.csv

--2024-08-04 02:55:49--  https://media.githubusercontent.com/media/fahriyegrl/ISIC-2024_skin_cancer_detection/master/train-metadata.csv
Resolving media.githubusercontent.com (media.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to media.githubusercontent.com (media.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 211794318 (202M) [text/plain]
Saving to: ‘train-metadata.csv’

train-metadata.csv  100%[===================>] 201.98M   180MB/s    in 1.1s    

2024-08-04 02:55:51 (180 MB/s) - ‘train-metadata.csv’ saved [211794318/211794318]



In [5]:
!wget https://raw.githubusercontent.com/fahriyegrl/ISIC-2024_skin_cancer_detection/main/test-metadata.csv
!wget https://github.com/fahriyegrl/ISIC-2024_skin_cancer_detection/raw/master/train-image.hdf5
!wget https://github.com/fahriyegrl/ISIC-2024_skin_cancer_detection/raw/main/test-image.hdf5

--2024-08-04 02:57:37--  https://raw.githubusercontent.com/fahriyegrl/ISIC-2024_skin_cancer_detection/main/test-metadata.csv
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2205 (2.2K) [text/plain]
Saving to: ‘test-metadata.csv’

test-metadata.csv   100%[===================>]   2.15K  --.-KB/s    in 0s      

2024-08-04 02:57:37 (20.9 MB/s) - ‘test-metadata.csv’ saved [2205/2205]

--2024-08-04 02:57:37--  https://github.com/fahriyegrl/ISIC-2024_skin_cancer_detection/raw/master/train-image.hdf5
Resolving github.com (github.com)... 140.82.116.3
Connecting to github.com (github.com)|140.82.116.3|:443... connected.
HTTP request sent, awaiting response... 302 Found
Location: https://media.githubusercontent.com/media/fahriyegrl/ISIC-2024_skin_cancer_detection/mast

In [38]:
import torch
from torch.utils.data import DataLoader
from torchvision import transforms
import os

# Paths to train/test HDF5 and CSV files
train_hdf5_file = 'train-image.hdf5'
test_hdf5_file = 'test-image.hdf5'
train_metadata_csv = 'train-metadata.csv'
test_metadata_csv = 'test-metadata.csv'

train_hdf5_file

'train-image.hdf5'

In [41]:
try:
    with h5py.File(train_hdf5_file, 'r') as file:
        print(f"Train HDF5 file successfully opened. Keys:\n{list(file.keys())}")
except Exception as e:
    print(f"Error opening {train_hdf5_file}: {e}")

Train HDF5 file successfully opened. Keys:
['ISIC_0015670', 'ISIC_0015845', 'ISIC_0015864', 'ISIC_0015902', 'ISIC_0024200', 'ISIC_0035502', 'ISIC_0051648', 'ISIC_0051665', 'ISIC_0051710', 'ISIC_0051758', 'ISIC_0051812', 'ISIC_0051822', 'ISIC_0051896', 'ISIC_0051897', 'ISIC_0051958', 'ISIC_0051983', 'ISIC_0052003', 'ISIC_0052004', 'ISIC_0052026', 'ISIC_0052042', 'ISIC_0052068', 'ISIC_0052094', 'ISIC_0052109', 'ISIC_0052122', 'ISIC_0052164', 'ISIC_0052205', 'ISIC_0052213', 'ISIC_0052220', 'ISIC_0052231', 'ISIC_0052241', 'ISIC_0052259', 'ISIC_0052270', 'ISIC_0052310', 'ISIC_0052313', 'ISIC_0052328', 'ISIC_0052332', 'ISIC_0052355', 'ISIC_0052357', 'ISIC_0052367', 'ISIC_0061318', 'ISIC_0062556', 'ISIC_0065755', 'ISIC_0067881', 'ISIC_0068212', 'ISIC_0070972', 'ISIC_0071851', 'ISIC_0071852', 'ISIC_0073261', 'ISIC_0073270', 'ISIC_0073301', 'ISIC_0073316', 'ISIC_0073364', 'ISIC_0073396', 'ISIC_0073412', 'ISIC_0073426', 'ISIC_0073467', 'ISIC_0073505', 'ISIC_0073511', 'ISIC_0073521', 'ISIC_007352

In [21]:
train_metadata.dtypes


isic_id                          object
target                            int64
patient_id                       object
age_approx                      float64
sex                              object
anatom_site_general              object
clin_size_long_diam_mm          float64
image_type                       object
tbp_tile_type                    object
tbp_lv_A                        float64
tbp_lv_Aext                     float64
tbp_lv_B                        float64
tbp_lv_Bext                     float64
tbp_lv_C                        float64
tbp_lv_Cext                     float64
tbp_lv_H                        float64
tbp_lv_Hext                     float64
tbp_lv_L                        float64
tbp_lv_Lext                     float64
tbp_lv_areaMM2                  float64
tbp_lv_area_perim_ratio         float64
tbp_lv_color_std_mean           float64
tbp_lv_deltaA                   float64
tbp_lv_deltaB                   float64
tbp_lv_deltaL                   float64
tbp_lv_deltaLB                  float64
tbp_lv_deltaLBnorm              float64
tbp_lv_eccentricity             float64
tbp_lv_location                  object
tbp_lv_location_simple           object
tbp_lv_minorAxisMM              float64
tbp_lv_nevi_confidence          float64
tbp_lv_norm_border              float64
tbp_lv_norm_color               float64
tbp_lv_perimeterMM              float64
tbp_lv_radial_color_std_max     float64
tbp_lv_stdL                     float64
tbp_lv_stdLExt                  float64
tbp_lv_symm_2axis               float64
tbp_lv_symm_2axis_angle           int64
tbp_lv_x                        float64
tbp_lv_y                        float64
tbp_lv_z                        float64
attribution                      object
copyright_license                object
lesion_id                        object
iddx_full                        object
iddx_1                           object
iddx_2                           object
iddx_3                           object
iddx_4                           object
iddx_5                           object
mel_mitotic_index                object
mel_thick_mm                    float64
tbp_lv_dnn_lesion_confidence    float64
dtype: object

In [24]:
import pandas as pd
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from sklearn.pipeline import Pipeline
import numpy as np

#train_metadata.head(), test_metadata.head()
label_column = "target"
feature_columns = [col for col in train_metadata.columns if col != label_column and col != "isic_id" and col != "patient_id"
                   and col != "image_type" and col != "attribution" and col != "copyright_license"  ]

feature_columns_test = [col for col in test_metadata.columns if col != "isic_id" and col != "patient_id"
                   and col != "image_type" and col != "attribution" and col != "copyright_license"  ]


train_features = train_metadata[feature_columns]
train_labels = train_metadata[label_column]

test_features = test_metadata[feature_columns_test]
#test_labels = test_metadata[label_column]

categorical_features = train_features.select_dtypes(include=['object']).columns.tolist()
numerical_features = train_features.select_dtypes(include=['int64', 'float64']).columns.tolist()

categorical_features_test = test_features.select_dtypes(include=['object']).columns.tolist()
numerical_features_test = test_features.select_dtypes(include=['int64', 'float64']).columns.tolist()

preprocessor_train = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(), numerical_features),
        ('cat', OneHotEncoder(), categorical_features)
    ])

preprocessor_test = ColumnTransformer(
    transformers=[
        ('num', StandardScaler(), numerical_features_test),
        ('cat', OneHotEncoder(), categorical_features_test)
    ])

preprocessor_train.fit(train_features)
train_features_processed = preprocessor_train.transform(train_features)

preprocessor_test.fit(test_features)
test_features_processed = preprocessor_test.transform(test_features)

train_features_processed_df = pd.DataFrame(train_features_processed)
test_features_processed_df = pd.DataFrame(test_features_processed)

train_features_processed_df.head()
#test_features_processed_df.head()






(                                                   0
 0    (0, 0)\t0.14614533641392255\n  (0, 1)\t-0.51...
 1    (0, 0)\t0.14614533641392255\n  (0, 1)\t-1.62...
 2    (0, 0)\t0.14614533641392255\n  (0, 1)\t-0.30...
 3    (0, 0)\t0.5138965705425961\n  (0, 1)\t-0.407...
 4    (0, 0)\t-0.22160589771475098\n  (0, 1)\t-0.6...,
          0         1         2         3         4         5         6   \
 0 -0.267261 -0.346339  0.475801  0.714282 -1.356418 -1.094750 -0.360907   
 1 -1.069045 -1.014280 -1.391248 -1.414189  1.024760 -0.227959 -1.003738   
 2  1.336306  1.360619  0.915447  0.699908  0.331658  1.322709  1.364645   
 
          7         8         9   ...        33   34   35   36   37   38   39  \
 0  0.477004 -0.732209 -0.795808  ...  1.408956  0.0  1.0  0.0  1.0  1.0  0.0   
 1 -1.391477  1.413913  1.410335  ... -0.598970  1.0  0.0  1.0  0.0  1.0  1.0   
 2  0.914472 -0.681704 -0.614528  ... -0.809986  0.0  1.0  0.0  1.0  1.0  0.0   
 
     40   41   42  
 0  1.0  0.0  1.0  
 1 

In [57]:
import h5py
import torch
import torch.nn as nn
import torch.optim as optim
import torchvision.transforms as transforms
from torchvision.models import vit_b_16
from torch.utils.data import Dataset, DataLoader
from PIL import Image
import numpy as np
import io
from sklearn.preprocessing import StandardScaler

class SkinHDF5DatasetTrain(Dataset):
  def __init__(self, hdf5_file, metadata_csv, preprocessor, label_column, transform=None):
    self.file = h5py.File(hdf5_file, 'r')
    #print(self.file.keys())
    self.transform = transform
    self.metadata = pd.read_csv(metadata_csv)
    self.label_column = label_column
    self.preprocessor = preprocessor


    self.metadata.sort_values('isic_id', inplace=True)
    self.image_keys = self.metadata['isic_id'].tolist()

    metadata_features = self.metadata.drop(columns=[self.label_column, 'isic_id', 'patient_id', 'image_type', 'attribution', 'copyright_license'])
    self.features_processed = self.preprocessor.transform(metadata_features)

    self.labels = self.metadata[label_column].astype(int).values



  def __len__(self):
    return len(self.image_keys)

  def __getitem__(self, id):
    image_key = self.image_keys[id]
    image_bytes = self.file[image_key][()]
    image= Image.open(io.BytesIO(image_bytes)).convert('RGB')

    if self.transform:
      image = self.transform(image)

    label = self.labels[id]
    metadata = self.features_processed[id]

    label = torch.tensor(label, dtype=torch.long)
    metadata = torch.tensor(metadata.toarray(), dtype=torch.float32)

    return image, label, metadata


class SkinHDF5DatasetTest(Dataset):
  def __init__(self, hdf5_file, metadata_csv, preprocessor,transform=None):
    self.file = h5py.File(hdf5_file, 'r')
    self.transform = transform
    self.metadata = pd.read_csv(metadata_csv)
    self.label_column = label_column
    self.preprocessor = preprocessor


    self.metadata.sort_values('isic_id', inplace=True)
    self.image_keys = self.metadata['isic_id'].tolist()

    metadata_features = self.metadata.drop(columns=['isic_id', 'patient_id', 'image_type', 'attribution', 'copyright_license'])
    self.features_processed = self.preprocessor.transform(metadata_features)


  def __len__(self):
    return len(self.image_keys)

  def __getitem__(self, id):
    image_key = self.image_keys[id]
    image_bytes = self.file[image_key][()]
    image= Image.open(io.BytesIO(image_bytes)).convert('RGB')

    if self.transform:
      image = self.transform(image)

    label = self.labels[id]
    metadata = self.features_processed[id]

    label = torch.tensor(label, dtype=torch.long)
    metadata = torch.tensor(metadata.toarray(), dtype=torch.float32)

    return image, label, metadata




In [58]:
# Initialize datasets and dataloaders
train_dataset = SkinHDF5DatasetTrain(train_hdf5_file,train_metadata_csv, preprocessor_train,label_column, transform=skin_transform)
train_loader = DataLoader(train_dataset, batch_size=32, shuffle=True)

test_dataset = SkinHDF5DatasetTest(test_hdf5_file, test_metadata_csv,preprocessor_test, transform=skin_transform)
test_loader = DataLoader(test_dataset, batch_size=32, shuffle=False)

<ipython-input-57-ee83da7a5abb>:18: DtypeWarning: Columns (51,52) have mixed types. Specify dtype option on import or set low_memory=False.
  self.metadata = pd.read_csv(metadata_csv)


In [60]:
for image, label, metadata in train_loader:
    print("Sample image tensor values:", image[0])  # Print the values of the first image tensor
    print("Sample label value:", label[0].item())  # Print the first label value
    print("Sample metadata values:", metadata[0])

Sample image tensor values: tensor([[[ 0.6627,  0.6706,  0.6941,  ...,  0.7333,  0.7569,  0.7647],
         [ 0.6314,  0.6392,  0.6706,  ...,  0.7333,  0.7647,  0.7725],
         [ 0.5765,  0.6000,  0.6314,  ...,  0.7412,  0.7725,  0.7961],
         ...,
         [ 0.7647,  0.7647,  0.7412,  ...,  0.6706,  0.6235,  0.5922],
         [ 0.7255,  0.7333,  0.7333,  ...,  0.6941,  0.6549,  0.6314],
         [ 0.6941,  0.7098,  0.7333,  ...,  0.7098,  0.6784,  0.6549]],

        [[ 0.1529,  0.1608,  0.1843,  ...,  0.2784,  0.2863,  0.2863],
         [ 0.1216,  0.1294,  0.1608,  ...,  0.2784,  0.2941,  0.2941],
         [ 0.0667,  0.0902,  0.1216,  ...,  0.2863,  0.3098,  0.3176],
         ...,
         [ 0.2078,  0.2000,  0.1765,  ...,  0.3098,  0.2235,  0.1686],
         [ 0.1843,  0.1922,  0.2000,  ...,  0.3333,  0.2549,  0.2078],
         [ 0.1765,  0.1922,  0.2157,  ...,  0.3412,  0.2706,  0.2314]],

        [[-0.1608, -0.1529, -0.1294,  ..., -0.1137, -0.0824, -0.0667],
         [-0.1922

KeyboardInterrupt: 